In [1]:
import pandas as pd
import datetime
import random
import os
import gc

from datetime import datetime
import calendar

import matplotlib.pyplot as plt

import numpy as np

from bokeh.palettes import Spectral10
from bokeh.io import output_notebook, show

output_notebook()

pd.set_option('display.max_columns', None)
pd.set_option('display.width', 1000)

palette = Spectral10

pd.set_option('display.float_format', lambda x: '%.3f' % x)

import bokeh
bokeh.__version__

os.chdir("/home/tales/dev/mdc_analysis/")
print("working dir", os.getcwd())

from src.dao.csv_dao import load_user_gps_csv
from src.dao.dbdao import DBDAO

Loading BokehJS ...

working dir /home/tales/dev/mdc_analysis


In [2]:
def local_time(data, time_col="time", tz_col="tz"):
    data["local_" + time_col] = data[time_col] + data[tz_col]
    return data

def load_users_gps_data(userids):
    df = pd.DataFrame()
    for userid in userids:
        user_gps_df = load_user_gps_csv(userid)
        user_gps_df["userid"] = [userid] * len(user_gps_df)
        df = df.append(user_gps_df)
        
    df = local_time(df)
    df = df[["userid", "latitude", "longitude", "tz", "time", "local_time"]].sort_values("local_time")

    return df

def load_user_gps_data(user_id):
    user_gps_data = load_user_gps_csv(user_id)
    user_gps_data["userid"] = [user_id] * len(user_gps_data)
    user_gps_data = local_time(user_gps_data)
    
    user_gps_data = user_gps_data[["userid", "latitude", "longitude", "tz", "time", "local_time"]].sort_values("local_time")
    return user_gps_data

In [3]:
n_sample = 10

userids = DBDAO().users_with_places().sample(n_sample).tolist()

userids = 5950,5936,6037,6104,6177,5973,5980,5942,6026,6073

# Categoria HOME (pela tabela places)

In [4]:
from src.plot.plot import plot_user_loc
from bokeh.plotting import gridplot

def places_home(userid, user_gps_data):
    if len(DBDAO().places_home_df(userid=userid)) == 0:
        return pd.DataFrame()
    
    home_visit_data = DBDAO().places_home_df(userid=userid).sort_values("time_start")
    return places(home_visit_data, user_gps_data)

def places_home_friend(userid, user_gps_data):
    if len(DBDAO().places_home_friend_df(userid=userid)) == 0:
        return pd.DataFrame()
    
    home_friend_visit_data = DBDAO().places_home_friend_df(userid=userid).sort_values("time_start")
    return places(home_friend_visit_data, user_gps_data)

def places_work(userid, user_gps_data):
    if len(DBDAO().places_work_df(userid=userid)) == 0:
        return pd.DataFrame()
    
    work_visit_data = DBDAO().places_work_df(userid=userid).sort_values("time_start")
    return places(work_visit_data, user_gps_data)

def places(place_label_visit_data, user_gps_data):
    place_label_visit_data = local_time(place_label_visit_data, time_col="time_start", tz_col="tz_start")
    place_label_visit_data = local_time(place_label_visit_data, time_col="time_end", tz_col="tz_end")

    user_visit_locations = pd.DataFrame()

    for index, row in place_label_visit_data.iterrows():
        user_visit_locations = user_visit_locations.append(user_gps_data[(user_gps_data["local_time"] >= row[
            "local_time_start"]) & (user_gps_data["local_time"] <= row["local_time_end"])])
        
    return user_visit_locations

def plot_visit(visit_locations, color="navy", title="user home visits"):
    p = plot_user_loc(visit_locations[["latitude", "longitude"]].drop_duplicates(), title, width=400, height=300, size=4, color=color)
    return p

In [ ]:
i = 0
grid = [[]]
for user_id in userids:
    user_gps_data = load_user_gps_data(user_id)
    user_home_locations = places_home(user_id, user_gps_data)
    user_work_locations = places_work(user_id, user_gps_data)
    
    if user_home_locations.empty or user_work_locations.empty:
        continue
    
    user_home_locations = user_home_locations[["longitude", "latitude"]].drop_duplicates()
    user_work_locations = user_work_locations[["longitude", "latitude"]].drop_duplicates()
    
    print(user_id, len(user_home_locations), len(user_work_locations))
    
    if len(user_home_locations) > 500:
        user_home_locations = user_home_locations.sample(500)

    if len(user_home_locations) > 500:
        user_work_locations = user_work_locations.sample(500)    
    
    p_home = plot_visit(user_home_locations, color="navy", title=str(user_id) + " HOME visits")
    p_work = plot_visit(user_work_locations, color="magenta", title=str(user_id) + " WORK visits")
    
    if i % 2 == 0:
        grid.append([])
        
    grid[-1].append(p_home)
    i += 1
    grid[-1].append(p_work)
    i += 1
    p_home = None
    gc.collect()

show(gridplot(grid))

# Categoria HOME por dia da semana (pela tabela places)

In [ ]:
def enrich_time_columns(gps_data, time_col="local_time"):
    gps_data["hour"] = [datetime.utcfromtimestamp(gps_time).hour for gps_time in gps_data[time_col]]
    gps_data["min"] = [datetime.utcfromtimestamp(gps_time).minute for gps_time in gps_data[time_col]]
    gps_data["sec"] = [datetime.utcfromtimestamp(gps_time).second for gps_time in gps_data[time_col]]
    gps_data["weekday"] = [calendar.day_name[datetime.utcfromtimestamp(gps_time).weekday()] for gps_time in gps_data[time_col]]
    gps_data["local_datetime"] = [datetime.utcfromtimestamp(gps_time).strftime('%Y-%m-%d %H:%M:%S') for gps_time in gps_data[time_col]]
    
    return gps_data


In [ ]:
from bokeh.plotting import show, gridplot
from bokeh.models import Range1d
from bokeh.palettes import Category20

def plot_home_by_weekday(user_id):
    user_gps_data = load_user_gps_data(user_id)
    user_home_locations = places_home(user_id, user_gps_data)
    
    user_home_locations = enrich_time_columns(user_home_locations)
    
    i = 0
    grid = [[]]
    for weekday in user_home_locations.weekday.drop_duplicates().tolist():
        print(weekday)
        p = plot_user_loc(user_home_locations[user_home_locations["weekday"] == weekday][["latitude", "longitude"]].drop_duplicates(), str(user_id) + " user home location: " + weekday, color=Category20[7][i], width=300, height=300)

        if i % 3 == 0:
            grid.append([])
        grid[-1].append(p)
        i += 1
        p = None
        gc.collect()

    return gridplot(grid)


show(plot_home_by_weekday(5936))



In [ ]:
show(plot_home_by_weekday(5980))

# Categoria HOME com inferencia pela hora

In [ ]:
user_id = 5936
user_gps_data = load_user_gps_data(user_id)
user_home_locations = enrich_time_columns(places_home(user_id, user_gps_data))

p_home_inferred = user_home_locations[(user_home_locations["hour"] >= 3) & (user_home_locations["hour"] <=4)]

show(plot_visit(p_home_inferred, color="navy", title=str(5936) + "HOME visits"))

In [ ]:
user_id = 5980
user_gps_data = load_user_gps_data(user_id)
user_home_locations = enrich_time_columns(places_home(user_id, user_gps_data))

p_home_inferred = user_home_locations[(user_home_locations["hour"] >= 3) & (user_home_locations["hour"] <=4)]

show(plot_visit(p_home_inferred, color="navy", title=str(5980) + "HOME visits"))

# Categoria HOME OF FRIEND

In [9]:
i = 0
grid = [[]]
for user_id in userids:
    user_gps_data = load_user_gps_data(user_id)
    user_home_locations = places_home(user_id, user_gps_data)
    user_home_friend_locations = places_home_friend(user_id, user_gps_data)
    
    if user_home_locations.empty or user_home_friend_locations.empty:
        continue
    
    user_home_locations = user_home_locations[["longitude", "latitude"]].drop_duplicates()
    user_home_friend_locations = user_home_friend_locations[["longitude", "latitude"]].drop_duplicates()
    
    print(user_id, len(user_home_locations), len(user_home_friend_locations))
    
    if len(user_home_locations) > 500:
        user_home_locations = user_home_locations.sample(500)

    if len(user_home_locations) > 500:
        user_home_friend_locations = user_home_friend_locations.sample(500)    
    
    p_home = plot_visit(user_home_locations, color="navy", title=str(user_id) + " HOME visits")
    p_home_friend = plot_visit(user_home_friend_locations, color="green", title=str(user_id) + " WORK visits")
    
    if i % 2 == 0:
        grid.append([])
        
    grid[-1].append(p_home)
    i += 1
    grid[-1].append(p_home_friend)
    i += 1
    p_home = None
    gc.collect()

show(gridplot(grid))

5950 246 137
6037 1722 105
6104 497 40
6177 2809 442
5973 172 3
5980 1252 33
